<h1>Содержание<span class="tocSkip"></span></h1>
</ul></li><li><span><a href="#Подготовка" data-toc-modified-id="Подготовка-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Подготовка</a></span></li><li><span><a href="#Анализ" data-toc-modified-id="Анализ-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Анализ</a></span></li><li><span><a href="#Обучение" data-toc-modified-id="Обучение-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Обучение</a></span></li><li><span><a href="#Тестирование" data-toc-modified-id="Тестирование-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Тестирование</a></span></li><li><span><a href="#Чек-лист-проверки" data-toc-modified-id="Чек-лист-проверки-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Чек-лист проверки</a></span></li></ul></div>

#  Прогнозирование заказов такси

Компания «Чётенькое такси» собрала исторические данные о заказах такси в аэропортах. Чтобы привлекать больше водителей в период пиковой нагрузки, нужно спрогнозировать количество заказов такси на следующий час. 

Для этого необходимо:

1. Загрузить данные и выполнить их ресемплирование по одному часу.
2. Проанализировать данные.
3. Обучить разные модели с различными гиперпараметрами. Сделать тестовую выборку размером 10% от исходных данных.
4. Проверить данные на тестовой выборке и сделать выводы.

## Подготовка

Перед началом работы сделаем импорт всех необходимых библиотек.

In [1]:
import pandas as pd
import numpy as np
import warnings

import time
import plotly.graph_objects as go
import plotly.express as px

from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.stattools import adfuller
import statsmodels.api as sm

from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score, TimeSeriesSplit, cross_validate
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, make_scorer

<div class="alert alert-block alert-success">
<b>Успех:</b> Отлично, что все импорты собраны в первой ячейке ноутбука! Если у того, кто будет запускать твой ноутбук будут отсутствовать некоторые библиотеки, то он это увидит сразу, а не в процессе!
</div>

Загрузим необходимые данные и выведим несколько строк для наглядности. Попутно сделаем ресеплиинг по дню и сделаем дату индексом.

In [2]:
df = pd.read_csv('/datasets/taxi.csv', index_col = [0], parse_dates=[0])
df.sort_index()
df = df.resample('1H').sum()

display(df.head(3))

num_orders
datetime                       
2018-03-01 00:00:00         124
2018-03-01 01:00:00          85
2018-03-01 02:00:00          71

Имеются исторические данные в разрезе дня (с март по август 2018 года включительно) заказов такси. 
Распределение данных наглядно выведим на график (предварительно написав функцию -- использовать ее будем несколько раз):

In [3]:
def autoScatter(df, cols, title, metr):
    df_copy = df.copy()
    print()
#     добавляем необходимые метрики
    if metr == 1:
        df_copy['std'] = df_copy[cols].rolling(12).std()
        df_copy['mean'] = df_copy[cols].rolling(12).mean()
    
#     удаляем пустые значения
    df_copy = df_copy.dropna()
    
#     визуализируем
    data = []
    cols_list = cols + ['std', 'mean'] if metr == 1 else cols

    for c in cols_list:
        fig_n = go.Scatter({'x': df_copy.index,'y': df_copy[c], 'name': c})
        data.append(fig_n)
        
    fig = go.Figure(data=data)
    fig.update_layout(title_text = title, title_x=0.5)
    fig.show()

In [4]:
autoScatter(df, ['num_orders'], 'Распределение временного ряда', 1)

## Анализ

Посмотрим на данные в рамках тренда, сезонности и остатка. Посмотрим на графики за последний месяц.

In [5]:
decomposed = seasonal_decompose(df['2018-08-01':'2018-08-31'])

In [6]:
autoScatter(decomposed.trend.to_frame(), ['trend'], 'Trend of last month', 1)

In [7]:
autoScatter(decomposed.seasonal.to_frame(), ['seasonal'], 'Seasonality of last month', 1)

In [8]:
autoScatter(decomposed.resid.to_frame(), ['resid'], 'Resid of last month', 1)

Сезонность статическая в рамках суток, случайная часть имеет постоянное среднее значение, но иногда все таки есть всплески. А тренд показывает постепенный рост количества заказов такси с течением времени, это можно проследить в течение всех исторических данных:

In [9]:
autoScatter(seasonal_decompose(df).trend.to_frame(), ['trend'], 'Trend of last month', 1)

Заметим, что линия тренда имеет некоторый шум.

Посмотрим на распределение признаков в выборке:

In [10]:
fig = px.histogram(df, x = 'num_orders', marginal='box')
fig.update_layout(title_text='Describe', title_x=0.5)
fig.show()

Есть длинный правый "ус", что говорит о выбросах. Убирать их не стоит, так как есть пиковые нагрузки на вызов такси.
Модель стоит строить на стационарном ряде, поэтому проверим наш с помощью теста Дики-Фуллера. Если необходимо, сделаем ряд стационарным через логарифмирование или дифференцирование.

In [11]:
DF_test = adfuller(df.num_orders)
print(f'adf: {DF_test[0]}')
print(f'P-value: {DF_test[1]}')
print(f'Critical values: {DF_test[4]}')

print('Есть единичные корни, ряд не стационарен' if DF_test[0]> DF_test[4]['5%'] else 'Единичных корней нет, ряд стационарен')

adf: -3.0689242890279558
P-value: 0.028940051402612906
Critical values: {'1%': -3.431842162413052, '5%': -2.8621993540813637, '10%': -2.567120978470452}
Единичных корней нет, ряд стационарен


Так как adf больше 5%, значит единичных корней нет, ряд стационарен.

## Обучение

Создадим обучающие признаки с помощью функции `make_features`: выделим год, месяц, день и день недели во временном ряду. А еще добавим признаки отстающего значения (**lag**) и окно **rolling_mean_size** для скользящего среднего.

In [12]:
def make_features(data, max_lag, rolling_mean_size):
    ''' Создание обучающих признаков: день недели
    '''
    df = data.copy()
    df['dayofweek'] = df.index.dayofweek
    
    for lag in range(1, max_lag + 1):
        df['lag_{}'.format(lag)] = df['num_orders'].shift(lag)

    df['rolling_mean'] = df['num_orders'].shift().rolling(rolling_mean_size).mean()
    
    return df

Разделим данные на обучающую и тестовую выборки

In [13]:
train, test = train_test_split(df, shuffle=False, test_size=0.1)

train = train.dropna()

Попробуем предсказать новые значения предыдущим:

In [14]:
pred_previous = test.shift()
pred_previous.iloc[0] = train.iloc[-1]
rmse_base =  mean_squared_error(test['num_orders'], pred_previous) ** 0.5

print("RMSE предыдущим значением:", round(rmse_base, 2))

RMSE предыдущим значением: 58.86


И посмотрим предсказания по среднему значению:

In [15]:
pred_mean = np.ones(test.shape) * train['num_orders'].mean()
rmse_base = mean_squared_error(test['num_orders'], pred_mean) ** 0.5
print("RMSE по среднему:", round(rmse_base, 2))

RMSE по среднему: 84.74


Покажем результаты на графике:

In [16]:
df_out = pd.merge(test, 
                  pred_previous, 
                  how = 'left', 
                  left_index = True, 
                  right_index = True, 
                  suffixes=('_data', '_prev_pred'))['2018-08-01':'2018-08-31']

df_out['num_orders_mean_pred'] = pred_mean

In [17]:
autoScatter(df_out, ['num_orders_data', 'num_orders_prev_pred', 'num_orders_mean_pred'], 
            'Предсказание предыдущим значением и по среднему за последний месяц', 0)

Предсказания по предыдущему значению лучше.

Напишем вспомогательную функцию `split` для получения сплита выборки на обучающую и тестовую в соотношении 9:1 (10% тестовой выборки).

In [18]:
def split(data):
    ''' Создание обучающей, тестовой выборки в пропорции 9:1
    '''
    RANDOM_STATE = 1234
    
    train, test = train_test_split(data, shuffle=False, test_size=0.1, random_state=RANDOM_STATE)
    train = train.dropna()
    
    X_trian = train.drop('num_orders', axis = 1)
    X_test = test.drop('num_orders', axis = 1) 
    y_train = train.num_orders
    y_test = test.num_orders
    
    return X_trian, X_test, y_train, y_test

А потом подключается функция `model_fit` обучения модели и вычисления метрики `RMSE`:

In [19]:
def rmse(y, y_pred):
    ''' Подготовка метрики 
    '''
    return mean_squared_error(y, y_pred) ** 0.5

rmse_score = make_scorer(rmse, greater_is_better = False)

In [20]:
def model_fit(ml, lag, roll_size):
    ''' Обучение моделей и получение предсказаний
    '''
    X_trian, X_test, y_train, y_test = split(df)
    
    model = ml.fit(X_trian, y_train)

    rmse_train = rmse(y_train, model.predict(X_trian))
    rmse_test = rmse(y_test, model.predict(X_test)) 
    
    return rmse_train

напишем функцию для подбора параметров лага и скользящего среднего для каждой модели:

In [21]:
def select_params(model, df):
    best_lag, best_roll_size, best_rmse = 0, 0, 48

    for lag in range(1, 51, 5):
        for roll_size in range(1, 51, 5):

            df = make_features(df, lag, roll_size)       
            
            if model == 'LR':
                rmse = model_LR(df)
            elif model == 'DT':
                rmse = model_DT(df)
            else:
                rmse = model_RF(df) # при создании модели используется кросс-валидация

            if rmse < best_rmse:
                best_rmse, best_lag, best_roll_size = rmse.round(2), lag, roll_size
                break

    print(f'{best_lag = }, {best_roll_size = }, {best_rmse = }')

Подберем параметры для **Линейной регрессии**:

In [22]:
def model_LR(df):
    ''' Обучение модели Линейной регрессии
    '''
#     делим выборку тест и обучающуую выборки с выделением целевого и остальных признаков
    X_trian, X_test, y_train, y_test = split(df)

#     обучаем модель на обучающей выборке
    model_LR = LinearRegression().fit(X_trian, y_train)
 
    cv = TimeSeriesSplit(n_splits=8)

#     используем кросс-валидацию
    rmse_LR = cross_val_score(model_LR, 
                             X_trian, 
                             y_train, 
                             scoring = rmse_score, 
                             cv = cv)

    return abs(rmse_LR.mean())

In [23]:
%%time
select_params('LR',df)

best_lag = 46, best_roll_size = 1, best_rmse = 26.19
CPU times: user 11.8 s, sys: 28.7 s, total: 40.5 s
Wall time: 40.5 s


Аналогично для **Дерева решений**:

In [34]:
def model_DT(df):
    ''' Обучение модели Дерева решений
    '''
#     делим выборку тест и обучающуую выборки с выделением целевого и остальных признаков
    X_trian, X_test, y_train, y_test = split(df)

#     обучаем модель на обучающей выборке
    model_DT = DecisionTreeRegressor()
     
    cv = TimeSeriesSplit(n_splits=8)
    
    param_grid = {'min_samples_split': range(2, 20, 2), 
                  'min_samples_leaf': range(2, 20, 2), 
                  'max_depth': range(4, 20, 2)}

    clf = GridSearchCV(model_DT, 
                       scoring = rmse_score, 
                       param_grid = param_grid,
                       n_jobs=4,
                       cv=tscv).fit(X_trian, y_train)
    
#     model_DT = DecisionTreeRegressor(min_samples_split = clf.best_params_.get('min_samples_split'), 
#                                            min_samples_leaf = clf.best_params_.get('min_samples_leaf'),
#                                            max_depth = clf.best_params_.get('max_depth')).fit(X_trian, y_train)

    model_DT = DecisionTreeRegressor(min_samples_split = 2, min_samples_leaf = 18, max_depth = 6).fit(X_trian, y_train)
    rmse_DT = cross_val_score(model_DT, 
                             X_trian, 
                             y_train, 
                             scoring = rmse_score, 
                             cv = cv)
    
    return abs(rmse_DT.mean())

In [31]:
%%time
X_trian, X_test, y_train, y_test = split(df)

model_DT = DecisionTreeRegressor()

tscv = TimeSeriesSplit(n_splits=8)

param_grid = {'min_samples_split': range(2, 20, 2), 
              'min_samples_leaf': range(2, 20, 2), 
              'max_depth': range(4, 20, 2)}

# используем кросс-валидацию GridSearchCV 
clf = GridSearchCV(model_DT, 
                   scoring = rmse_score, 
                   param_grid = param_grid, 
                   n_jobs=4, 
                   cv=tscv).fit(X_trian, y_train)
clf.best_params_

CPU times: user 7.34 s, sys: 833 ms, total: 8.17 s
Wall time: 4min 36s


{'max_depth': 6, 'min_samples_leaf': 18, 'min_samples_split': 2}

<div class="alert alert-block alert-success">
<b>Успех (ревью 2):</b> Тут все верно.
</div>

Подобрав параметры, попробуем обучить с ними модель:

In [35]:
%%time
select_params('DT',df)

best_lag = 46, best_roll_size = 1, best_rmse = 29.23
CPU times: user 1min 17s, sys: 7.9 s, total: 1min 25s
Wall time: 47min 41s


Итого:
* модель Случайного леса показала лучший RMSE, но время обучения слишком велико. Для данной модели необходимо применить 65 лагов и 11 окно для скользящего среднего
* Дерево решений показало отличный RMSE  с 96 лагом и 6 окнами
* Линейная регрессия в лиделах по соотношению качества модели и времени обучения. Для нее нужно 46 лагов и одно окно.

## Тестирование

Посмотрим на итоговый результат Линейной регрессии: уже известны параметры модели, по ним построим график соотношения цели ииз тестовой выборки и предсказания.

In [36]:
df = make_features(df, 46, 1)
X_trian, X_test, y_train, y_test = split(df)
model = LinearRegression().fit(X_trian, y_train)

preds_test = pd.Series(model.predict(X_test), index = y_test.index, name='preds')
df_preds = pd.concat([y_test, preds_test], axis=1)

In [37]:
fig1 = go.Scatter({'x': df_preds.index,'y': df_preds['num_orders'], 'name': 'y_test'})
fig2 = go.Scatter({'x': df_preds.index,'y': df_preds['preds'], 'name': 'preds_test'})
data = [fig1, fig2]
fig = go.Figure(data=data)
fig.update_layout(title_text='Test and Predicts', title_x=0.5)
fig.show()

Кажется, модель неплохо справляется с предсказанием, но все-таки есть пики, которые она не показывает (наверно, высокая загруженность такси в выходные дни так же следовало учесть).